Project 1 - California Water Usage
=================

Welcome to the first project in Data 8! We will be exploring possible connections between water usage, geography, and income in California. The water data for this project was procured from the [California State Water Resources Control Board](http://www2.pacinst.org/gpcd/table.html) and curated by the [Pacific Institute](http://pacinst.org/). The map data includes [US topography](https://github.com/jgoodall/us-maps), [California counties](https://github.com/johan/world.geo.json/tree/master/countries/USA/CA), and [ZIP codes](http://bl.ocks.org/jefffriesen/6892860).

The dataset on income comes from the IRS ([documentation](http://www.irs.gov/pub/irs-soi/13zpdoc.doc)).  We have identified some interesting columns in the dataset, but a full description of all the columns (and a definition of the population in the dataset and some interesting anonymization procedures they used) is available in this [description](irs_info.pdf).

In [1]:
# Run this cell, but please don't change it.

import numpy as np
import math
from datascience import *

# These lines set up the plotting functionality and formatting.
import matplotlib
matplotlib.use('Agg', warn=False)
%matplotlib inline
import matplotlib.pyplot as plots
plots.style.use('fivethirtyeight')

First, load the data. Loading may take some time.

In [2]:
# Run this cell, but please don't change it.

districts = Map.read_geojson('water_districts.geojson')
zips = Map.read_geojson('ca_zips.geojson.gz')
usage_raw = Table.read_table('water_usage.csv', dtype={'pwsid': str})
income_raw = Table.read_table('ca_income_by_zip.csv', dtype={'ZIP': str}).drop(['STATEFIPS', 'STATE', 'agi_stub'])
wd_vs_zip = Table.read_table('wd_vs_zip.csv', dtype={'PWSID': str, 'ZIP': str}).set_format([2, 3], PercentFormatter)

Part 0: Maps
======

The `districts` and `zips` data sets are `Map` objects. Documentation on mapping in the `datascience` package can be found at [data8.org/datascience/maps.html](http://data8.org/datascience/maps.html).  To view a map of California's water districts, run the cell below. Click on a district to see its description.

In [3]:
districts.format(width=400, height=200)

In [4]:
district_table = Table.from_records(districts.features)
district_table.show(3)

**Question 0.0** Draw a map of the Alameda County Water District (row 0) and the East Bay Municipal Utilities District (row 2).

In [5]:
alameda_and_east_bay = [district_table.column(1).item(0), district_table.column(1).item(2)]
Map(alameda_and_east_bay, height=300, width=300)

Part 1: California Income
=======

Let's look at the `income_raw` table.

In [6]:
income_raw

ZIP   | N1    | MARS1 | MARS2 | MARS4 | PREP  | N2    | NUMDEP | A00100 | N02650 | A02650 | N00200 | A00200 | N00300 | A00300 | N00600 | A00600 | N00650 | A00650 | N00700 | A00700 | N00900 | A00900 | N01000 | A01000 | N01400 | A01400 | N01700 | A01700 | SCHF | N02300 | A02300 | N02500 | A02500 | N26270 | A26270 | N02900 | A02900 | N03220 | A03220 | N03300 | A03300 | N03270 | A03270 | N03150 | A03150 | N03210 | A03210 | N03230 | A03230 | N03240 | A03240 | N04470 | A04470 | A00101 | N18425 | A18425 | N18450 | A18450 | N18500 | A18500 | N18300 | A18300 | N19300 | A19300 | N19700 | A19700 | N04800 | A04800 | N05800 | A05800 | N09600 | A09600 | N07100 | A07100 | N07300 | A07300 | N07180 | A07180 | N07230 | A07230 | N07240 | A07240 | N07220 | A07220 | N07260 | A07260 | N09400 | A09400 | N10600 | A10600 | N59660 | A59660 | N59720 | A59720 | N11070 | A11070 | N10960 | A10960 | N06500 | A06500 | N10300 | A10300 | N85330 | A85330 | N85300 | A85300 | N11901 | A11901 | N11902 | A11902
90001 | 13100 | 6900  | 1890  | 4270  | 10740 | 29670 | 15200  | 181693 | 13100  | 184344 | 10220  | 142287 | 640    | 96     | 50     | 69     | 30     | 20     | 180    | 55     | 3490   | 31751  | 70     | -17    | 60     | 382    | 380    | 3001   | 0    | 950    | 4493   | 80     | 123    | 30     | 105    | 3510   | 2651   | 20     | 6      | 0      | 0      | 0      | 0      | 0      | 0      | 150    | 119    | 60     | 98     | 0      | 0      | 510    | 7212   | 8498   | 170    | 95     | 270    | 154    | 340    | 952    | 500    | 1424   | 340    | 3168   | 240    | 363    | 4200   | 20798  | 4190   | 2176   | 0      | 0      | 1800   | 623    | 0      | 0      | 70     | 28     | 520    | 248    | 240    | 39     | 1020   | 304    | 0      | 0      | 3290   | 4659   | 12180  | 37759  | 6320   | 20531  | 5880   | 16995  | 6500   | 8805   | 1230   | 980    | 2680   | 1554   | 5800   | 6197   | 0      | 0      | 0      | 0      | 1220   | 856    | 11480  | 32934
90001 | 5900  | 1700  | 1970  | 2210  | 4960  | 17550 | 9690   | 203628 | 5900   | 204512 | 5610   | 188556 | 830    | 68     | 60     | 32     | 70     | 19     | 660    | 351    | 540    | 5917   | 60     | 111    | 50     | 489    | 310    | 4450   | 0    | 460    | 2522   | 210    | 947    | 40     | 831    | 700    | 885    | 50     | 12     | 0      | 0      | 0      | 0      | 50     | 152    | 200    | 154    | 50     | 81     | 0      | 0      | 1260   | 20442  | 46800  | 800    | 1023   | 430    | 505    | 810    | 2383   | 1250   | 4605   | 820    | 7172   | 870    | 1620   | 5300   | 74352  | 5290   | 8710   | 0      | 0      | 3380   | 2947   | 0      | 0      | 370    | 249    | 620    | 518    | 630    | 114    | 2520   | 2047   | 20     | 6      | 410    | 982    | 5820   | 23531  | 2160   | 4562   | 1890   | 3948   | 2520   | 4160   | 600    | 441    | 3180   | 5762   | 3460   | 6754   | 0      | 0      | 0      | 0      | 530    | 797    | 5360   | 17656
90001 | 1480  | 330   | 760   | 390   | 1240  | 4710  | 2470   | 89065  | 1480   | 89344  | 1440   | 82579  | 400    | 32     | 20     | 12     | 0      | 0      | 460    | 477    | 130    | 1351   | 40     | 1      | 40     | 660    | 140    | 2599   | 0    | 150    | 892    | 60     | 670    | 0      | 0      | 210    | 279    | 50     | 14     | 0      | 0      | 0      | 0      | 0      | 0      | 90     | 76     | 0      | 0      | 0      | 0      | 680    | 13264  | 41920  | 540    | 1329   | 120    | 294    | 500    | 1453   | 680    | 3591   | 490    | 4248   | 560    | 1296   | 1470   | 49298  | 1470   | 6618   | 0      | 0      | 900    | 1488   | 0      | 0      | 120    | 90     | 180    | 198    | 80     | 11     | 750    | 1163   | 20     | 7      | 80     | 232    | 1470   | 8950   | 0      | 0      | 0      | 0      | 190    | 256    | 170    | 132    | 1290   | 5131   | 1310   | 5417   | 0      | 0      | 0      | 0      | 230    | 520    | 1250   | 4050
90001 | 330   | 50    | 210   | 70    | 290   | 1100

Some observations:

1. The table contains several numerical columns and a column for the ZIP code.
2. For each ZIP code, there are 6 rows.  Each row for a ZIP code has data from tax returns in one *income bracket* -- a group of people who make between some income and some other income.  
3. According to the IRS documentation, all the numerical columns are *totals* -- either total numbers of returns that fall into various categories, or total amounts of money (in thousands of dollars) from returns in those categories.  For example, the column `'N02650'` is the number of returns that included a total income amount, and `'A02650'` is the total amount of total income (in thousands of dollars) from those returns.

**Question 1.0.** Since we don't care about income brackets, but we do care about totals per ZIP code, let's group together our income data by ZIP code. Assign the name `income_by_zipcode` to a table with just one row per ZIP code. When you group according to ZIP code, the remaining columns should be summed. In other words, for any other column such as `'N02650'`, the value of `'N02650'` in a row corresponding to ZIP code 90210 (for example) should be the sum of the values of `'N02650'` in the 6 rows of `income_raw` corresponding to ZIP code 90210.

In [7]:
income_by_zipcode = income_raw.group("ZIP", sum)
income_by_zipcode

ZIP   | N1 sum | MARS1 sum | MARS2 sum | MARS4 sum | PREP sum | N2 sum | NUMDEP sum | A00100 sum  | N02650 sum | A02650 sum  | N00200 sum | A00200 sum  | N00300 sum | A00300 sum | N00600 sum | A00600 sum | N00650 sum | A00650 sum | N00700 sum | A00700 sum | N00900 sum | A00900 sum | N01000 sum | A01000 sum | N01400 sum | A01400 sum | N01700 sum | A01700 sum | SCHF sum | N02300 sum | A02300 sum | N02500 sum | A02500 sum | N26270 sum | A26270 sum | N02900 sum | A02900 sum | N03220 sum | A03220 sum | N03300 sum | A03300 sum | N03270 sum | A03270 sum | N03150 sum | A03150 sum | N03210 sum | A03210 sum | N03230 sum | A03230 sum | N03240 sum | A03240 sum | N04470 sum | A04470 sum | A00101 sum  | N18425 sum | A18425 sum | N18450 sum | A18450 sum | N18500 sum | A18500 sum | N18300 sum | A18300 sum | N19300 sum | A19300 sum | N19700 sum | A19700 sum | N04800 sum | A04800 sum  | N05800 sum | A05800 sum | N09600 sum | A09600 sum | N07100 sum | A07100 sum | N07300 sum | A07300 sum | N07180 sum | A07180 sum | N07230 sum | A07230 sum | N07240 sum | A07240 sum | N07220 sum | A07220 sum | N07260 sum | A07260 sum | N09400 sum | A09400 sum | N10600 sum | A10600 sum | N59660 sum | A59660 sum | N59720 sum | A59720 sum | N11070 sum | A11070 sum | N10960 sum | A10960 sum | N06500 sum | A06500 sum | N10300 sum | A10300 sum | N85330 sum | A85330 sum | N85300 sum | A85300 sum | N11901 sum | A11901 sum | N11902 sum | A11902 sum
90001 | 20970  | 9010      | 4930      | 6980      | 17360    | 53540  | 28170      | 527457      | 20970      | 531772      | 17740      | 456544      | 2070       | 241        | 170        | 208        | 130        | 68         | 1530       | 1258       | 4220       | 40103      | 190        | 183        | 150        | 1531       | 890        | 11571      | 0        | 1600       | 8137       | 380        | 2338       | 90         | 3903       | 4520       | 4161       | 120        | 32         | 0          | 0          | 0          | 0          | 50         | 152        | 470        | 370        | 110        | 179        | 0          | 0          | 2790       | 49827      | 136004      | 1820       | 4543       | 850        | 1020       | 1910       | 5712       | 2770       | 13037      | 1900       | 17162      | 1950       | 4222       | 11460      | 180741      | 11440      | 24020      | 30         | 124        | 6350       | 5583       | 0          | 0          | 610        | 404        | 1380       | 1030       | 950        | 164        | 4530       | 3897       | 40         | 13         | 3820       | 6064       | 19960      | 77235      | 8480       | 25093      | 7770       | 20943      | 9210       | 13221      | 2050       | 1594       | 7640       | 18417      | 11060      | 24663      | 0          | 0          | 0          | 0          | 2110       | 3164       | 18460      | 56128
90002 | 18960  | 8230      | 3830      | 6800      | 15120    | 47200  | 24850      | 462823      | 18960      | 467128      | 15910      | 396088      | 1960       | 227        | 170        | 72         | 130        | 30         | 1450       | 1196       | 4310       | 40865      | 170        | 257        | 130        | 985        | 950        | 14167      | 0        | 1450       | 7131       | 360        | 2344       | 30         | 116        | 4610       | 4305       | 130        | 29         | 0          | 0          | 0          | 0          | 60         | 161        | 470        | 411        | 100        | 202        | 0          | 0          | 2910       | 50033      | 133338      | 1880       | 3809       | 900        | 1003       | 2070       | 5698       | 2890       | 12370      | 2100       | 18397      | 2060       | 5197       | 10070      | 153993      | 10060      | 19696      | 20         | 24         | 5660       | 4942       | 0          | 0          | 610        | 403        | 1350       | 1006       | 810        | 138        | 3910       | 3362       | 50         | 15         | 3900       | 6159       | 18270      

**Question 1.1.** Relabel the columns in `income_by_zipcode` to match the labels in `income_raw`; you probably modified all the names slightly in the previous question. 

In [10]:
for label in income_by_zipcode.labels:
    income_by_zipcode.relabel(label, label.replace('sum', '')).relabel(label, label.replace(' ', ''))
income_by_zipcode

ZIP   | N1    | MARS1 | MARS2 | MARS4 | PREP  | N2    | NUMDEP | A00100      | N02650 | A02650      | N00200 | A00200      | N00300 | A00300 | N00600 | A00600 | N00650 | A00650 | N00700 | A00700 | N00900 | A00900 | N01000 | A01000 | N01400 | A01400 | N01700 | A01700 | SCHF | N02300 | A02300 | N02500 | A02500 | N26270 | A26270 | N02900 | A02900 | N03220 | A03220 | N03300 | A03300 | N03270 | A03270 | N03150 | A03150 | N03210 | A03210 | N03230 | A03230 | N03240 | A03240 | N04470 | A04470 | A00101      | N18425 | A18425 | N18450 | A18450 | N18500 | A18500 | N18300 | A18300 | N19300 | A19300 | N19700 | A19700 | N04800 | A04800      | N05800 | A05800 | N09600 | A09600 | N07100 | A07100 | N07300 | A07300 | N07180 | A07180 | N07230 | A07230 | N07240 | A07240 | N07220 | A07220 | N07260 | A07260 | N09400 | A09400 | N10600 | A10600 | N59660 | A59660 | N59720 | A59720 | N11070 | A11070 | N10960 | A10960 | N06500 | A06500 | N10300 | A10300 | N85330 | A85330 | N85300 | A85300 | N11901 | A11901 | N11902 | A11902
90001 | 20970 | 9010  | 4930  | 6980  | 17360 | 53540 | 28170  | 527457      | 20970  | 531772      | 17740  | 456544      | 2070   | 241    | 170    | 208    | 130    | 68     | 1530   | 1258   | 4220   | 40103  | 190    | 183    | 150    | 1531   | 890    | 11571  | 0    | 1600   | 8137   | 380    | 2338   | 90     | 3903   | 4520   | 4161   | 120    | 32     | 0      | 0      | 0      | 0      | 50     | 152    | 470    | 370    | 110    | 179    | 0      | 0      | 2790   | 49827  | 136004      | 1820   | 4543   | 850    | 1020   | 1910   | 5712   | 2770   | 13037  | 1900   | 17162  | 1950   | 4222   | 11460  | 180741      | 11440  | 24020  | 30     | 124    | 6350   | 5583   | 0      | 0      | 610    | 404    | 1380   | 1030   | 950    | 164    | 4530   | 3897   | 40     | 13     | 3820   | 6064   | 19960  | 77235  | 8480   | 25093  | 7770   | 20943  | 9210   | 13221  | 2050   | 1594   | 7640   | 18417  | 11060  | 24663  | 0      | 0      | 0      | 0      | 2110   | 3164   | 18460  | 56128
90002 | 18960 | 8230  | 3830  | 6800  | 15120 | 47200 | 24850  | 462823      | 18960  | 467128      | 15910  | 396088      | 1960   | 227    | 170    | 72     | 130    | 30     | 1450   | 1196   | 4310   | 40865  | 170    | 257    | 130    | 985    | 950    | 14167  | 0    | 1450   | 7131   | 360    | 2344   | 30     | 116    | 4610   | 4305   | 130    | 29     | 0      | 0      | 0      | 0      | 60     | 161    | 470    | 411    | 100    | 202    | 0      | 0      | 2910   | 50033  | 133338      | 1880   | 3809   | 900    | 1003   | 2070   | 5698   | 2890   | 12370  | 2100   | 18397  | 2060   | 5197   | 10070  | 153993      | 10060  | 19696  | 20     | 24     | 5660   | 4942   | 0      | 0      | 610    | 403    | 1350   | 1006   | 810    | 138    | 3910   | 3362   | 50     | 15     | 3900   | 6159   | 18270  | 73561  | 8960   | 27858  | 8300   | 23004  | 8710   | 12170  | 2280   | 1943   | 6520   | 14756  | 10180  | 21012  | 0      | 0      | 0      | 0      | 1630   | 2176   | 17040  | 55190
90003 | 26180 | 11310 | 5130  | 9640  | 20570 | 64470 | 33760  | 612733      | 26180  | 618848      | 21680  | 518846      | 2410   | 393    | 220    | 100    | 170    | 39     | 1690   | 1339   | 6240   | 59400  | 230    | 275    | 170    | 1528   | 1120   | 16814  | 0    | 1880   | 9002   | 490    | 3204   | 90     | 1173   | 6490   | 6102   | 150    | 39     | 0      | 0      | 30     | 97     | 90     | 262    | 560    | 477    | 160    | 284    | 0      | 0      | 3300   | 57436  | 147488      | 2110   | 4120   | 1000   | 1089   | 2250   | 6165   | 3280   | 13216  | 2290   | 21225  | 2260   | 5650   | 13410  | 196510      | 13410  | 24756  | 20     | 19     | 7510   | 6410   | 0      | 0      | 780    | 497    | 1780   | 1335   | 1060   | 184    | 5210   | 4347   | 50     | 13     | 5620   | 8885   | 25030  | 95254  | 11910  | 36094  | 10940  | 29504  | 11950  | 16777  | 3190   | 2789   | 8680   | 18348  | 13880  | 27416  | 0      | 0      | 0 

**Question 1.2.**
Create a table called `income` with  one row per ZIP code and the following columns.

1. A `ZIP` column with the same contents as `'ZIP'` from `income_by_zipcode`.
2. A `returns` column containing the total number of tax returns that include a total income amount (column `'N02650'` from `income_by_zipcode`).
3. A `total` column containing the total income in all tax returns in thousands of dollars (column `'A02650'` from `income_by_zipcode`).
4. A `farmers` column containing the number of farmer returns (column `'SCHF'` from `income_by_zipcode`).

In [11]:
income = Table().with_columns([
        ('ZIP', income_by_zipcode.column('ZIP')),
        ('returns', income_by_zipcode.column('N02650')),
        ('total', income_by_zipcode.column('A02650')),
        ('farmers', income_by_zipcode.column('SCHF'))
        ])
income.set_format('total', NumberFormatter(0)).show(5)

**Question 1.3.** What is the average total income reported on all California tax returns that include a total income amount? **Express the answer in *dollars* as an `int` rounded to the nearest dollar.**

In [12]:
int((np.sum(income.column('total') * 1000) / np.sum(income.column('returns'))).round())

72832

**Question 1.4.** All ZIP codes with less than 100 returns (or some other special conditions) are grouped together into one ZIP code with a special code. Remove the row for that ZIP code from the `income` table. *Hint:* This ZIP code value has far more returns than any of the other ZIP codes.

In [13]:
income = income.where(income.column('returns') != max(income.column('returns')))
income

ZIP   | returns | total      | farmers
90001 | 20970   | 531,772    | 0
90002 | 18960   | 467,128    | 0
90003 | 26180   | 618,848    | 0
90004 | 27360   | 1,649,431  | 0
90005 | 15430   | 717,290    | 0
90006 | 22630   | 571,157    | 0
90007 | 11710   | 315,581    | 0
90008 | 14710   | 668,523    | 0
90010 | 2210    | 320,471    | 0
90011 | 36670   | 864,961    | 0
... (1472 rows omitted)

**Question 1.5**. Among the tax returns in California for ZIP codes represented in the `incomes` table, is there an association between income and living in a ZIP code with a higher-than-average proportion of farmers?

Answer the question by comparing the average incomes for two groups of *tax returns*: those in ZIP codes with a greater-than-average proportion of farmers and those in ZIP codes with a less-than-average (or average) proportion. Make sure both of these values are displayed (preferably in a table). *Then, describe your findings.*

In [14]:
# Build and display a table with two rows:
#   1) incomes of returns in ZIP codes with a greater-than-average proportion of farmers
#   2) incomes of returns in other ZIP codes
farm_proportion = income.column('farmers')/income.column('returns')
income_by_farm_proportion = income.with_column('farm proportion', farm_proportion)

mean_farm_proportion = np.mean(farm_proportion)

less_than_average_farmers = income_by_farm_proportion.where(income_by_farm_proportion.column('farm proportion') < mean_farm_proportion)
more_than_average_farmers = income_by_farm_proportion.where(income_by_farm_proportion.column('farm proportion') > mean_farm_proportion)

less = np.mean(np.sum(less_than_average_farmers.column('total') * 1000) / np.sum(less_than_average_farmers.column('returns')))
more = np.mean(np.sum(more_than_average_farmers.column('total') * 1000) / np.sum(more_than_average_farmers.column('returns')))


average_income_across_proportions = Table().with_columns(['Less Farmers', less,
                                                         'More Farmers', more])
average_income_across_proportions

Less Farmers | More Farmers
73916.7      | 60427.7

Yes, there is an association between income and living in a ZIP code with a higher-than average proportion of farmers.
As can be seen in the table above, the average income in areas where there are less farmers is substantially greater than the average income in areas where there are more farmers.

**Question 1.6.** Investigate the same question by comparing two histograms: the average incomes of ZIP codes that have above-average vs below-average proportions of farmers. Quantify and describe the difference in the [standard deviations](www.inferentialthinking.com/chapter3/spread.html) of average incomes for the two kinds of ZIP codes.

<img src="https://i.imgur.com/jicA2to.png"/>

In [15]:
# Compute and compare the spread of both distributions
more_farmers_SD = np.std(1000 * more_than_average_farmers.column(2)/more_than_average_farmers.column(1))
less_farmers_SD = np.std(1000 * less_than_average_farmers.column(2)/less_than_average_farmers.column(1))
print(more_farmers_SD, less_farmers_SD)

26121.6872364 78380.8883511


There is a noticeable large difference in the spread of average income between the zip codes with higher proportions of farmers and lower proportions of farmers. The histogram for the income of zip codes with higher proportions of farmers is skewed right with a peak around $55,000. The tail for this histogram is much shorter and ends at around $175,000. In contrast, the histogram for the zip codes of areas with lower proportions of farmers is more spread out and flatter. This histogram is also skewed right, but its peak is much shorter and less pronounced than that of rht higher proportion histogram. Its tail continues on longer as well, reaching nearly $300,000. Looking at the standard deviations: the standard deviation for the higher proportion zip codes is almost three times less than that of the lower proportion areas. All together, this analysis shows that the incomes for areas with a higher proportion of famers are much less spread out and vary less than those in areas with lower proportions of farmers.

###### ZIP codes cover all the land in California and do not overlap. Here's a map of all of them.

<img src="california-zip-code-map.jpg" alt="CA ZIP Codes"/>

**Question 1.7.** Among the ZIP codes represented in the `incomes` table, is there an association between high average income and some aspect of the ZIP code's location? If so, describe one aspect of the location that is clearly associated with high income.

Answer the question by drawing a map of all ZIP codes that have an average income above 100,000 dollars. *Then, describe an association that you observe.*

In order to create a map of certain ZIP codes, you need to 
- Construct a table containing only the ZIP codes of interest, called `high_average_zips`,
- Join `high_average_zips` with the `zip_features` table to find the region for each ZIP code of interest,
- Call `Map(...)` on the column of features (provided).

In [16]:
# Write code to draw a map of only the high-income ZIP codes
zip_features = Table.from_records(zips.features)
high_average_zips = income.where(1000 * income.column(2)/income.column(1) > 100000)
high_zips_with_region = high_average_zips.join('ZIP', zip_features)
Map(list(high_zips_with_region.column('feature')), width=400, height=300)

There are quite a few ZIP codes that possess average incomes over 100,000 dollars, but the majority of them seem to be clustered in and around the Bay Area, and to a lesser extent, in and around Los Angeles. As such, I would say that there is an association between high average income and ZIP codes found in the Bay Area or Los Angeles regions. 

Part 2: Water Usage
======
We will now investigate water usage in California. The `usage` table contains three columns:

- `PWSID`: The Public Water Supply Identifier of the district
- `Population`: Estimate of average population served in 2015
- `Water`: Average residential water use (gallons per person per day) in 2014-2015

In [17]:
# Run this cell to create the usage table

usage_raw.set_format(4, NumberFormatter)
max_pop = usage_raw.select([0, 'population']).group(0, max).relabeled(1, 'Population')
avg_water = usage_raw.select([0, 'res_gpcd']).group(0, np.mean).relabeled(1, 'Water')
usage = max_pop.join('pwsid', avg_water).relabeled(0, 'PWSID')
usage

PWSID   | Population | Water
0110001 | 340000     | 70.7
0110003 | 57450      | 90.2727
0110005 | 1390000    | 76
0110006 | 151037     | 57.1818
0110008 | 73067      | 96.6364
0110009 | 79547      | 68.6364
0110011 | 31994      | 85.8182
0310003 | 23347      | 82.8182
0410002 | 101447     | 142
0410005 | 11208      | 88.8182
... (401 rows omitted)

**Question 2.1.** Draw a map of the water districts, colored by the per capita water usage in each district.

Use the `districts.color(...)` method to generate the map. It takes as its first argument a two-column table with one row per district that has the district `PWSID` as its first column. The label of the second column is used in the legend of the map, and the values are used to color each region.

In [18]:
per_capita_usage = usage.drop('Population')
districts.color(per_capita_usage, key_on='feature.properties.PWSID') 

**Question 2.2.** Based on the map above, which part of California appears to use more water per person, the San Francisco area or the Los Angeles area? 

Based on the map above, where the San Francisco area is predominantly yellow-colored and the Los Angeles region is predominantly orange-colored, Los Angeles appears to use more water per person.

Next, we will try to match each ZIP code with a water district. ZIP code boundaries do not always line up with water districts, and one water district often covers multiple ZIP codes, so this process is imprecise. It is even the case that some water districts overlap each other. Nonetheless, we can continue our analysis by matching each ZIP code to the water district with the largest geographic overlap.

The table `wd_vs_zip` describes the proportion of land in each ZIP code that is contained in each water district and vis versa. (The proportions are approximate because they do not correctly account for discontiguous districts, but they're mostly accurate.)

In [24]:
wd_vs_zip.show(20)

**Question 2.3.** Complete the `district_for_zip` function that takes a ZIP code. It returns the PWSID with the largest value of `ZIP in District` for that `zip_code`, if that value is at least 50%. Otherwise, it returns the string `'No District'`.

In [20]:
def district_for_zip(zip_code):
    zip_code = str(zip_code) # Ensure that the ZIP code is a string, not an integer
    districts = wd_vs_zip.where(wd_vs_zip.column('ZIP') == zip_code).sort('ZIP in District', descending=True)
    if (districts.num_rows > 0): 
        at_least_half = districts.column('ZIP in District').item(0) > 0.5
    else: 
        at_least_half = False
    if at_least_half:
        return districts.column('PWSID').item(0)
    else:
        return 'No District'

district_for_zip(94709)

'0110005'

This function can be used to associate each ZIP code in the `income` table with a `PWSID` and discard ZIP codes that do not lie (mostly) in a water district.

In [21]:
zip_pwsids = income.apply(district_for_zip, 'ZIP')
income_with_pwsid = income.with_column('PWSID', zip_pwsids).where(zip_pwsids != "No District")
income_with_pwsid.set_format(2, NumberFormatter(0)).show(5)

**Question 2.4.** Create a table called `district_data` with one row per PWSID and the following columns:

- `PWSID`: The ID of the district
- `Population`: Population estimate
- `Water`: Average residential water use (gallons per person per day) in 2014-2015
- `Income`: Average income in dollars of all tax returns in ZIP codes that are (mostly) contained in the district according to `income_with_pwsid`.

*Hint*: First create a `district_income` table that sums the incomes and returns for ZIP codes in each water district.

In [22]:
district_income = income_with_pwsid.group('PWSID', sum)
joined_with_usage_table = district_income.join('PWSID', usage)
table_with_income = joined_with_usage_table.with_column('Income', joined_with_usage_table.column('total sum') * 1000 / joined_with_usage_table.column('returns sum'))
table_with_income.set_format(['Population', 'Water', 'Income'], NumberFormatter(0))
district_data = table_with_income.select(['PWSID', 'Population', 'Water', 'Income'])
district_data

PWSID   | Population | Water | Income
0110001 | 340,000    | 71    | 79,032
0110005 | 1,390,000  | 76    | 82,497
0110006 | 151,037    | 57    | 52,924
0110008 | 73,067     | 97    | 163,257
0110009 | 79,547     | 69    | 133,902
0410002 | 101,447    | 142   | 50,401
0410006 | 18,300     | 286   | 38,721
0410011 | 9,615      | 92    | 44,707
0710001 | 106,455    | 110   | 53,551
0710003 | 197,536    | 102   | 73,914
... (200 rows omitted)

**Question 2.5.** The `bay_districts` table gives the names of all water districts in the San Francisco Bay Area. Is there an association between water usage and income among Bay Area water districts? Use the tables you have created to compare water usage between the 10 Bay Area water districts with the highest average income and the rest of the Bay Area districts, then describe the association. *Do not include any districts in your analysis for which you do not have income information.*

The names below are just suggestions; you may perform the analysis in any way you wish.

*Note*: Some Bay Area water districts may not appear in your `district_data` table. That's ok. Perform your analysis only on the subset of districts where you have both water usage & income information.

In [23]:
bay_districts = Table.read_table('bay_districts.csv')
joined_with_district_data_table = district_table.join('PWSID', district_data)
bay_water_vs_income = joined_with_district_data_table.join('popupContent', bay_districts, 'District')
bay_water_vs_income = bay_water_vs_income.sort('Income', descending=True)
top_10 = bay_water_vs_income.column('Water')[0:10]
rest = bay_water_vs_income.column('Water')[10:]
print(np.mean(top_10).round(2), np.mean(rest).round(2))
print(np.mean(top_10).round(2) - np.mean(rest).round(2))

92.76 68.12
24.64


*Complete this one-sentence conclusion:* In the Bay Area, people in the top 10 highest-income water districts used an average of `24.64` more gallons of water per person per day than people in the rest of the districts.

**Question 2.6.** In one paragraph, summarize what you have discovered through the analyses in this project and suggest what analysis should be conducted next to better understand California water usage, income, and geography. What additional data would be helpful in performing this next analysis?

Over this project, we learned about both the association between income and proportions of farmers in
an area and the association between location and water usage. In part one, the main takeaway was that in
areas where there are a larger than average proportion of farmers, the average income is about $13,000 less than in areas
where there are lower than average proportions of farmers. This suggests that on the average, farmers have lower incomes,
which thereby influences the average income of the areas in which farmers are more concentrated. In addition, by
looking at the map created in question 1.7, we can see that the higher income areas are concentrated around
locations with higher populations, which makes sense since these areas have less land available to farm and consequently
fewer farmers. Finally, because the standard deviation of areas with more farmers is lower than that of the
areas with less farmers, we can assume that salaries of farmers vary less than salaries of non-farmers. In
part two, we saw an association between location (San Francisco versus Los Angeles) and water usage. It
appears that people living near the Los Angeles area use more water than people living around the San
Francisco area. Additionally, we saw that in the Bay Area there is an association between income and water
usage. On average, the top ten highest income districts have a 24.64 gallon per capita usage higher than
the lower districts. To perform further analysis, one thing that would be helpful to have is the total set
of data for the Bay Area water districts and income. As not all of the data is present (as stated in the
directions), our calculations and the noticeable association may not be accurately representing the actual
association between income and water usage in the Bay Area. Having this additional information will allow
us to accurately complete the calculations to establish an association. Finally, having information on the
water usage in the analyzed areas in California during a drought could be an additional piece of information
that could help to establish an association between water usage and income. We would be able to see the
differences in decrease of usage in the higher and lower income areas, which would give further evidence that
there is a distinction between the two income levels.